In [14]:
import datetime
import re
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

from Project.Database import Db

In [15]:
year1_minutes, meta = Db.load_data(hourly=False, meta=True, year=1)
year2_minutes, meta = Db.load_data(hourly=False, meta=True, year=2)
year1_minutes

Timestamp  TimeStamp_Count  DHW_ClothesWasherColdFlow  \
0       2013-07-01 00:01:14-04:00                1                        0.0   
1       2013-07-01 00:02:14-04:00                2                        0.0   
2       2013-07-01 00:03:14-04:00                3                        0.0   
3       2013-07-01 00:04:14-04:00                4                        0.0   
4       2013-07-01 00:05:14-04:00                5                        0.0   
...                           ...              ...                        ...   
518787  2014-06-30 23:29:22-04:00           518788                        0.0   
518788  2014-06-30 23:30:22-04:00           518789                        0.0   
518789  2014-06-30 23:31:22-04:00           518790                        0.0   
518790  2014-06-30 23:59:22-04:00           518791                        0.0   
518791  2014-07-01 00:00:22-04:00           518792                        0.0   

        DHW_ClothesWasherHotFlow  DHW_DishwasherHotFlow  \
0                            0.0                0.00000   
1                            0.0                0.00000   
2                            0.0                0.00000   
3                            0.0                0.00000   
4                            0.0                0.00000   
...                          ...                    ...   
518787                       0.0                1.86261   
518788                       0.0                1.86261   
518789                       0.0                1.86261   
518790                       0.0                1.86261   
518791                       0.0                1.86261   

        DHW_HeatPumpWaterHeaterEnergyTotal  DHW_HeatPumpWaterHeaterPowerTotal  \
0                                 0.000000                           6.920000   
1                                 0.132000                           6.920000   
2                                 0.264000                           6.920000   
3                                 0.396000                           6.920000   
4                                 0.528000                           6.920000   
...                                    ...                                ...   
518787                         1074.687075                         765.920563   
518788                         1087.432650                         766.929871   
518789                         1100.200137                         768.525940   
518790                         1173.107485                           6.920000   
518791                         1173.239485                           6.920000   

        DHW_ManifoldColdFlow  DHW_ManifoldHotFlow  DHW_MixValveColdFlow  ...  \
0                   0.000000              0.00000               0.00000  ...   
1                   0.000000              0.00000               0.00000  ...   
2                   0.000000              0.00000               0.00000  ...   
3                   0.000000              0.00000               0.00000  ...   
4                   0.000000              0.00000               0.00000  ...   
...                      ...                  ...                   ...  ...   
518787             11.297412             57.77676               8.69218  ...   
518788             11.297412             57.77676               8.69218  ...   
518789             11.297412             57.77676               8.69218  ...   
518790             11.297412             57.77676               8.69218  ...   
518791             11.297412             57.77676               8.69218  ...   

        Vent_HRVTempReturnIn  Vent_HRVTempSupplyOut  \
0                  22.552117              23.758415   
1                  22.523656              23.737489   
2                  22.539345              23.742217   
3                  22.539554              23.727526   
4                  22.506425              23.705258   
...                      ...                    ...   
518787             23.9

In [16]:
#bath1 = meta.loc[(meta['Parameter'] == "Status_OnOff") & (meta['Measurement_Location'] == "Bath2") & (meta["Unnamed: 0"].str.contains('Status'))]['Unnamed: 0'].tolist()

In [17]:
# fig = px.scatter(year1_minutes, x="Timestamp", y=bath1)
# fig.show()

In [18]:
#Extract appliances from the meta data
appliance_condition = (lambda self: (
        (self["Parameter"] == "Status_OnOff") &
        (self["Subsystem"] == "Loads") &
        (~self["Unnamed: 0"].str.contains("Child")) &
        (~self["Unnamed: 0"].str.contains("Prnt")) &
        (~self["Unnamed: 0"].str.contains("StatusLatentload"))
))

appliances_statusOnOff = meta.loc[appliance_condition]["Unnamed: 0"].tolist()

appliance_location = meta.loc[appliance_condition][["Unnamed: 0", "Measurement_Location"]].sort_values(by="Measurement_Location", ascending=True).rename(columns={"Unnamed: 0": "Appliance"}).set_index("Appliance")

appliance_location

Measurement_Location
Appliance                                                
Load_StatusBA1Lights                                Bath1
Load_StatusBA2Lights                                Bath2
Load_StatusPlugLoadBR2Laptop                     Bedroom2
Load_StatusBR2Lights                             Bedroom2
Load_StatusPlugLoadBR3Laptop                     Bedroom3
Load_StatusBR3Lights                             Bedroom3
Load_StatusPlugLoadDesktopPCMonitor              Bedroom4
Load_StatusPlugLoadVacuum                        Bedroom4
Load_StatusBR4Lights                             Bedroom4
Load_StatusDRLights                           Dining Room
Load_StatusEntryHallLights                  Entry Hallway
Load_StatusPlugLoadToaster                        Kitchen
Load_StatusApplianceDishwasher                    Kitchen
Load_StatusPlugLoadCoffeeMaker                    Kitchen
Load_StatusPlugLoadCanOpener                      Kitchen
Load_StatusPlugLoadSlowCooker                     Kitchen
Load_StatusPlugLoadHandMixer                      Kitchen
Load_StatusApplianceOven                          Kitchen
Load_StatusApplianceCooktop                       Kitchen
Load_StatusPlugLoadToasterOven                    Kitchen
Load_StatusPlugLoadBlender                        Kitchen
Load_StatusApplianceRangeHood                     Kitchen
Load_StatusKitchenLightsC                         Kitchen
Load_StatusKitchenLightsB                         Kitchen
Load_StatusKitchenLightsA                         Kitchen
Load_StatusPlugLoadVideoGame                  Living Room
Load_StatusLRLights2                          Living Room
Load_StatusLRLights1                          Living Room
Load_StatusPlugLoadLRTV                       Living Room
Load_StatusPlugLoadLRBlueRay                  Living Room
Load_StatusLRLights3                          Living Room
Load_StatusMBALights                                MBath
Load_StatusPlugLoadHairDryerCurlIron                MBath
Load_StatusPlugLoadFan                     Master Bedroom
Load_StatusPlugLoadMBRBlueRay              Master Bedroom
Load_StatusPlugLoadHeatingPad              Master Bedroom
Load_StatusMBRLights1                      Master Bedroom
Load_StatusMBRLights2                      Master Bedroom
Load_StatusPlugLoadMBRTV                   Master Bedroom
Load_StatusPlugLoadIron                    Master Bedroom

In [19]:
#Combine minute data with the extracted appliances into a dataframe
minute_appliances_status = year1_minutes[["Timestamp"] + appliance_location.index.tolist()].copy()

In [20]:
#Replaces values to be binary 0 or 1.
for i in appliances_statusOnOff:
    minute_appliances_status.loc[minute_appliances_status[i] < 0, i] = 0
    minute_appliances_status.loc[minute_appliances_status[i] > 0, i] = 1
minute_appliances_status

Timestamp  Load_StatusBA1Lights  Load_StatusBA2Lights  \
0       2013-07-01 00:01:14-04:00                   0.0                   0.0   
1       2013-07-01 00:02:14-04:00                   0.0                   0.0   
2       2013-07-01 00:03:14-04:00                   0.0                   0.0   
3       2013-07-01 00:04:14-04:00                   0.0                   0.0   
4       2013-07-01 00:05:14-04:00                   0.0                   0.0   
...                           ...                   ...                   ...   
518787  2014-06-30 23:29:22-04:00                   0.0                   0.0   
518788  2014-06-30 23:30:22-04:00                   0.0                   0.0   
518789  2014-06-30 23:31:22-04:00                   0.0                   0.0   
518790  2014-06-30 23:59:22-04:00                   0.0                   0.0   
518791  2014-07-01 00:00:22-04:00                   0.0                   0.0   

        Load_StatusPlugLoadBR2Laptop  Load_StatusBR2Lights  \
0                                0.0                   0.0   
1                                0.0                   0.0   
2                                0.0                   0.0   
3                                0.0                   0.0   
4                                0.0                   0.0   
...                              ...                   ...   
518787                           0.0                   0.0   
518788                           0.0                   0.0   
518789                           0.0                   0.0   
518790                           0.0                   0.0   
518791                           0.0                   0.0   

        Load_StatusPlugLoadBR3Laptop  Load_StatusBR3Lights  \
0                                0.0                   0.0   
1                                0.0                   0.0   
2                                0.0                   0.0   
3                                0.0                   0.0   
4                                0.0                   0.0   
...                              ...                   ...   
518787                           0.0                   0.0   
518788                           0.0                   0.0   
518789                           0.0                   0.0   
518790                           0.0                   0.0   
518791                           0.0                   0.0   

        Load_StatusPlugLoadDesktopPCMonitor  Load_StatusPlugLoadVacuum  \
0                                       0.0                        0.0   
1                                       0.0                        0.0   
2                                       0.0                        0.0   
3                                       0.0                        0.0   
4                                       0.0                        0.0   
...                                     ...                        ...   
518787                                  0.0                        0.0   
518788                                  0.0                        0.0   
518789                                  0.0                        0.0   
518790                                  0.0                        0.0   
518791                                  0.0                        0.0   

        Load_StatusBR4Lights  ...  Load_StatusLRLights3  Load_StatusMBALights  \
0                        0.0  ...                   0.0                   0.0   
1                        0.0  ...                   0.0                   0.0   
2                        0.0  ...                   0.0                   0.0   
3                        0.0  ...                   0.0                   0.0   
4                        0.0  ...                   0.0                   0.0   
...                      ...  ...                   ...                   ...   
518787                   0.0  ...                   0.0                   0.0   
518788                  

In [21]:
appliance_job_list = []

for appliance in appliances_statusOnOff:
    name = " ".join(re.findall('[A-Z][^A-Z]*', appliance.split("Load_Status")[-1]))
    appliance_switch = minute_appliances_status[(minute_appliances_status[appliance] != minute_appliances_status[appliance].shift(1))][
                           ["Timestamp", appliance]][1:]

    df_indices = appliance_switch.index.tolist()
    for index, df_index in enumerate(df_indices):
        if appliance_switch.loc[df_index, appliance]:
            try:
                appliance_job_list.append({"appliance": name, "start": appliance_switch.loc[df_index, "Timestamp"], "end": appliance_switch.loc[df_indices[index+1], "Timestamp"], "location": appliance_location.loc[appliance, "Measurement_Location"]})
            except:
                continue

appliance_job_list

[{'appliance': 'B A1 Lights',
  'start': '2013-07-01 08:13:17-04:00',
  'end': '2013-07-01 08:18:17-04:00',
  'location': 'Bath1'},
 {'appliance': 'B A1 Lights',
  'start': '2013-07-01 18:00:31-04:00',
  'end': '2013-07-01 18:04:31-04:00',
  'location': 'Bath1'},
 {'appliance': 'B A1 Lights',
  'start': '2013-07-02 15:59:28-04:00',
  'end': '2013-07-02 16:04:28-04:00',
  'location': 'Bath1'},
 {'appliance': 'B A1 Lights',
  'start': '2013-07-02 18:00:28-04:00',
  'end': '2013-07-02 18:04:28-04:00',
  'location': 'Bath1'},
 {'appliance': 'B A1 Lights',
  'start': '2013-07-03 07:38:28-04:00',
  'end': '2013-07-03 07:43:28-04:00',
  'location': 'Bath1'},
 {'appliance': 'B A1 Lights',
  'start': '2013-07-03 21:36:27-04:00',
  'end': '2013-07-03 21:41:27-04:00',
  'location': 'Bath1'},
 {'appliance': 'B A1 Lights',
  'start': '2013-07-04 15:59:26-04:00',
  'end': '2013-07-04 16:04:26-04:00',
  'location': 'Bath1'},
 {'appliance': 'B A1 Lights',
  'start': '2013-07-04 18:00:26-04:00',
  'end

In [22]:
fig = px.timeline(appliance_job_list, x_start="start", x_end="end", y="appliance", color="location")
fig.write_html(Db.get_save_file_directory("Appliance_status_gantt.html"))


In [23]:
residens_condition = (lambda self: (
    (self["Subsystem"] == "Loads") &
    (self["Parameter"] == "Status_OnOff") &
    (self["Unnamed: 0"].str.contains("Sens"))
    )
)

residens_location = meta.loc[residens_condition]["Unnamed: 0"].tolist()

residens_location.sort()

In [24]:
person_status_list = []

for col in residens_location:
    name = "".join(re.findall("[PC][a-z]+[AB]", col))
    person_location = year1_minutes[lambda self: (self[col] != self[col].shift(1))][
                           ["Timestamp", col]][1:]

    df_indices = person_location.index.tolist()
    for index, df_index in enumerate(df_indices):
        if person_location.loc[df_index, col]:
            try:
                person_status_list.append({"appliance": name, "start": person_location.loc[df_index, "Timestamp"], "end": person_location.loc[df_indices[index+1], "Timestamp"], "location": "".join(col.split(name)[-1])})
            except:
                continue
person_status_list

[{'appliance': 'ChildA',
  'start': '2013-07-01 06:58:17-04:00',
  'end': '2013-07-01 07:58:17-04:00',
  'location': 'DOWN'},
 {'appliance': 'ChildA',
  'start': '2013-07-01 19:28:31-04:00',
  'end': '2013-07-01 20:13:31-04:00',
  'location': 'DOWN'},
 {'appliance': 'ChildA',
  'start': '2013-07-02 06:58:29-04:00',
  'end': '2013-07-02 07:58:29-04:00',
  'location': 'DOWN'},
 {'appliance': 'ChildA',
  'start': '2013-07-02 15:58:28-04:00',
  'end': '2013-07-02 16:28:28-04:00',
  'location': 'DOWN'},
 {'appliance': 'ChildA',
  'start': '2013-07-02 17:58:28-04:00',
  'end': '2013-07-02 18:28:28-04:00',
  'location': 'DOWN'},
 {'appliance': 'ChildA',
  'start': '2013-07-02 19:28:28-04:00',
  'end': '2013-07-02 20:13:28-04:00',
  'location': 'DOWN'},
 {'appliance': 'ChildA',
  'start': '2013-07-03 06:58:28-04:00',
  'end': '2013-07-03 07:58:28-04:00',
  'location': 'DOWN'},
 {'appliance': 'ChildA',
  'start': '2013-07-03 19:28:27-04:00',
  'end': '2013-07-03 20:13:27-04:00',
  'location': '

In [25]:
fig = px.timeline(person_status_list, x_start="start", x_end="end", y="appliance", color="location")
# fig.write_html(Db.get_save_file_directory("Person_status_gantt.html"))
fig.show()

In [26]:
fig = px.timeline(person_status_list+appliance_job_list, x_start="start", x_end="end", y="appliance", color="location")
# fig.show()



In [ ]:
fig.write_html(Db.get_save_file_directory("Person_appliance_status_gantt.html"))